In [1]:
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import copy
import os
import time

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [9]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [4]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos')
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_10
BIBF_01_16
BIBF_01_7
BIBF_03_16
BIBF_03_6
aktivin01_2
aktivin01_3
hipox03_2
melanoma_GF01_11
zometa01_4
zometa01_6
zometa02_4
zometa03_3
zometa03_5
zometa06_3


In [18]:
def DefineStartingAndEndingFrameOnHumanData(CellType, HumanDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  HumanAnnotFile = open(HumanAnnotPath,"r") 
  HumanAnnotList = HumanAnnotFile.readlines()

  StartingFrame = -1
  EndingFrame = 0

  for row in HumanAnnotList:
    splitted = row.split(' ')
    if splitted[0].isdigit():
      CurrentFrame = int(splitted[2])
      if CurrentFrame<StartingFrame or StartingFrame == -1:
        StartingFrame = CurrentFrame
      if CurrentFrame>EndingFrame:
        EndingFrame = CurrentFrame

  return [StartingFrame,EndingFrame]

In [33]:
def DefineStartingAndEndingFrameOnComputerData(CellType, NameModifier, ComputerDataFolder):
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 
  ComputerAnnotList = ComputerAnnotFile.readlines()

  StartingFrame = -1
  EndingFrame = 0

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    if splitted[0].isdigit():
      CurrentFrame = int(splitted[0].strip())
      if CurrentFrame<StartingFrame or StartingFrame == -1:
        StartingFrame = CurrentFrame
      if CurrentFrame>EndingFrame:
        EndingFrame = CurrentFrame

  return [StartingFrame,EndingFrame]

In [41]:
def GetFreq(AnnotData):
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      return AnnotData[cell_id][1].frame-AnnotData[cell_id][0].frame 
  return 1

In [6]:
#Reading the trajectories

def ReadData(CellType,NameModifier, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]

In [43]:
#Setting up parameters
#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
inp_video_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/"
out_video_path = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/04 Estimated Videos/"
ComputerDataFolder= "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/03 Estimated Paths/"
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/02 Human Annotations/"

FileNameModifier = "_mimic_human"
OnlyInRangeOfHumanData = False
OnlyInRangeOfComputerData = True
WriteCentres = False
WriteMovements = False
WriteMarkings = True
WriteHumanAnnotComp = True

In [44]:
# MAIN CODE

#Iterating through all the chosen cells

for CellType in CellTypes:
  print(CellType)
  #Setting up video writing

  cap = cv.VideoCapture(inp_video_path+CellType+".mpeg")
  ret, frame1 = cap.read()
  prvs = cv.cvtColor(frame1,cv.COLOR_BGR2GRAY)
  hsv = np.zeros_like(frame1)
  hsv[...,1] = 255

  #FRAME 2
  picture_number=1
  row=1

  #Video Write object
  frame_width=int(cap.get(3))
  frame_height=int(cap.get(4))

  if WriteCentres:
    out_centres = cv.VideoWriter(out_video_path + CellType +  FileNameModifier + "_centres.avi", cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  if WriteMovements:
    out_movements = cv.VideoWriter(out_video_path + CellType + FileNameModifier + "_movements.avi", cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  if WriteHumanAnnotComp:
    out_human_annot_comparison = cv.VideoWriter(out_video_path + CellType +  FileNameModifier + "_human_annot_comp.avi", cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))
  if WriteMarkings:
    out_marked_cells = cv.VideoWriter(out_video_path + CellType +  FileNameModifier + "_marked_cells.avi", cv.VideoWriter_fourcc('M','J','P','G'), 10, (frame_width, frame_height))

  FrameCounter = 0
  ret, frame2 = cap.read()

  [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,FileNameModifier,HumanDataFolder,ComputerDataFolder)
  HumanAnnotFreq = GetFreq(HumanAnnotData)
  [HumanStartFrame, HumanEndFrame] = DefineStartingAndEndingFrameOnHumanData(CellType,HumanDataFolder)
  [ComputerStartFrame, ComputerEndFrame] = DefineStartingAndEndingFrameOnComputerData(CellType,FileNameModifier,ComputerDataFolder)

  #------------ Starting the run for the individual video ------------

  while(ret):
  
    next1 = cv.cvtColor(frame2,cv.COLOR_BGR2GRAY)

    InHumanAnnotRange = False
    InComputerAnnotRange = False

    if FrameCounter>=HumanStartFrame and FrameCounter<=HumanEndFrame:
      InHumanAnnotRange = True
    if FrameCounter>=ComputerStartFrame and FrameCounter<=ComputerEndFrame:
      InComputerAnnotRange = True

    if ((not OnlyInRangeOfHumanData) or InHumanAnnotRange) and ((not OnlyInRangeOfComputerData) or InComputerAnnotRange):

      CentresImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
      MarkedCellsImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
      HumanAnnotCompImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
      MovementsImage = cv.cvtColor(next1, cv.COLOR_GRAY2BGR)
        
      H,W = next1.shape

      if FrameCounter%30==0: print("\tFrame "+str(FrameCounter))

      #------------ Showing the marked paths ------------   

      for cell_id in ComputerAnnotData.keys():
        for element in ComputerAnnotData[cell_id]:
          if element.frame == FrameCounter:
            CentresImage[
                          max([int(element.posy)-5,0]):
                          min([int(element.posy)+5,H]),
                          max([int(element.posx)-5,0]):
                          min([int(element.posx)+5,W])
                          ]=(255,0,255)
          if element.frame <= FrameCounter:
            for element2 in  ComputerAnnotData[cell_id]:
              if element2.frame == element.frame-1:
                cv.line(MovementsImage, tuple([element2.posx, element2.posy]), tuple([element.posx, element.posy]), (0,255,0),5)
                cv.line(HumanAnnotCompImage, tuple([element2.posx, element2.posy]), tuple([element.posx, element.posy]), (0,255,0),5)
                cv.line(MarkedCellsImage, tuple([element2.posx, element2.posy]), tuple([element.posx, element.posy]), (0+(element.id*37)%255,255,0+(element.id*29)%255), 5)

      for cell_id in HumanAnnotData.keys():
        for element in HumanAnnotData[cell_id]:
          if element.frame <= FrameCounter:
            for element2 in HumanAnnotData[cell_id]:
              if element2.frame == element.frame-HumanAnnotFreq:
                cv.line(HumanAnnotCompImage, tuple([element2.posx, element2.posy]), tuple([element.posx, element.posy]), (255,0,255),5)
      
      #------------ Writing the images into the videos ------------ 
      if WriteCentres:
        out_centres.write(CentresImage)
      if WriteMovements:
        out_movements.write(MovementsImage)
      if WriteHumanAnnotComp:
        out_human_annot_comparison.write(HumanAnnotCompImage)
      if WriteMarkings:
        out_marked_cells.write(MarkedCellsImage)
      
    ret, frame2 = cap.read()
      
    FrameCounter +=1

  cap.release()

  if WriteCentres:
    out_centres.release()
  if WriteMovements:
    out_movements.release()
  if WriteHumanAnnotComp:
    out_human_annot_comparison.release()
  if WriteMarkings:
    out_marked_cells.release()

  cv.destroyAllWindows()
  print()

print("Writing finished successfully")

BIBF06_10
	Frame 300
	Frame 330
	Frame 360

BIBF_01_16
	Frame 300
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510

BIBF_01_7
	Frame 300
	Frame 330

BIBF_03_16
	Frame 300
	Frame 330
	Frame 360

BIBF_03_6
	Frame 300
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540

aktivin01_2
	Frame 300
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540
	Frame 570

aktivin01_3
	Frame 300
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450

hipox03_2
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540
	Frame 570

melanoma_GF01_11
	Frame 300
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540
	Frame 570

zometa01_4
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540
	Frame 570
	Frame 600

zometa01_6
	Frame 330
	Frame 360
	Frame 390
	Frame 420
	Frame 450
	Frame 480
	Frame 510
	Frame 540
	Frame 